# Introduction

This tutorial will demonstrate how to use the QFieldCloud API to build custom applications and undertake analysis that use data stored and managed by a QFieldCloud instance. 

We'll introduce the QFieldCloud API and demonstrate how to use the qfieldcloud-sdk, a Python package and client to make requests to the QFieldCloud API. We'll use these tools to complete two tasks:

1. Create interactive chart and web map visualisations using QFieldCloud data.
2. Use QFieldCloud data in an accuracy assessment of the <a href="https://developers.google.com/earth-engine/datasets/catalog/ESA_WorldCover_v200" target="_blank">ESA World Cover v200</a> dataset.

Along the way we'll provide code snippets that illustrate how to use the qfieldcloud-sdk that you can expand upon for your own applications. 



## QFieldCloud API

QFieldCloud comes with a REST API which can be used to interact with projects and data stored in QFieldCloud. This supports various use cases including building web apps on top of data collected in-the-field using QField. 

The API for the hosted version of QFieldCloud can be found at: https://app.qfield.cloud/swagger/

The API for the QFieldCloud instance that will be used in this workshop can be found at: https://pgc.livelihoods-and-landscapes.com/swagger/

The QFieldCloud API has endpoints for authentication, managing users and teams, querying and managing projects, and querying and downloading project data.  

## QFieldCloud SDK

The qfieldcloud-sdk is the official client to connect to the QFieldCloud API. The qfieldcloud-sdk is a Python package and can be installed using `pip`:

```
pip install qfieldcloud-sdk
```

This makes it well suited for integrating QFieldCloud data in data analysis workflows that leverage other tools in the Python ecosystem (e.g. GeoPandas, sklearn) or web applications (e.g. Django, FastAPI; QFieldCloud is actually a Django application).

Both QFieldCloud and qfieldcloud-sdk are developed by OPENGIS.ch, the developers of QField. 

### Setup for Colab

If you are running this notebook using Google Colab you will need to uncomment the below lines and install qfieldcloud-sdk, geopandas, and rasterio. 

In [ ]:
!pip install qfieldcloud-sdk==0.6.1
!pip install geopandas
!pip install rasterio

### Import packages



In [114]:
import requests
import rasterio
import os
import plotly.express as px
import geopandas as gpd
from qfieldcloud_sdk import sdk
from pathlib import Path
from sklearn.metrics import accuracy_score
from sklearn.metrics import recall_score
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay

### Login

Create a `Client` object and login to QFieldCloud. The constructor function for a `Client` takes the URL for the QFieldCloud API as an argument.

Here, we pass in the URL for the api for QFieldCloud instance being used for this workshop: https://pgc.livelihoods-and-landscapes.com/api/v1/

In [65]:
# Create a client object
client = sdk.Client(
    url="https://pgc.livelihoods-and-landscapes.com/api/v1/",
)

The `Client` object has methods for authentication and querying users, projects, and data stored in QFieldCloud. First, let's login to our QFieldCloud instance. 

A successful login returns a token that can be used to make authenticated requests to the QFieldCloud API end points.

**For non-demonstration purposes, don't pass in credentials as clear text!**

In [66]:
# Authenticate using the client's login() method
client.login(
    username="demo_user",
    password="demo_user"
)

{'token': 'fQFwcBsPxlaAc8sSiVFIbk6uFhsHt9IANGoadxblmvgJaL4kqOvs1bBH1f0qaoyQiDviKg5haR2JMxhwyhIeDpUBtXoHyzvlba3t',
 'expires_at': '2022-12-23T11:51:59.788166+01:00',
 'username': 'demo_user',
 'user_type': '1',
 'email': 'demo_user@test.com',
 'avatar_url': None,
 'first_name': '',
 'last_name': '',
 'full_name': ''}

### Query projects

Call `list_projects()` on the authenticated `Client` object to get a list of the user's projects.

`list_projects()` returns a list of dictionary objects with project metadata including its id, name, owner, description, status, and the user's role on the project.

In [67]:
projects = client.list_projects()

In [68]:
projects

[{'id': '2127b0a8-ced6-4129-a56b-4e8edf332d3d',
  'name': 'demo-ground-truth',
  'owner': 'super_user',
  'description': '',
  'private': True,
  'is_public': False,
  'created_at': '2022-11-23T03:52:53.488231+01:00',
  'updated_at': '2022-11-23T10:14:22.404108+01:00',
  'data_last_packaged_at': '2022-11-23T07:45:15.331446+01:00',
  'data_last_updated_at': '2022-11-23T10:14:13.870895+01:00',
  'can_repackage': True,
  'needs_repackaging': True,
  'status': 'ok',
  'user_role': 'editor',
  'user_role_origin': 'collaborator'}]

### List project files

The `list_remote_files()` method can be used to list files associated with a project. The `list_remote_files()` method takes a `project_id` as an argument and returns a list of dictionary objects describing the project's files and the file versions. 

In [69]:
# list project files stored in QFieldCloud
files = client.list_remote_files(
    project_id="2127b0a8-ced6-4129-a56b-4e8edf332d3d"
)

In [70]:
# print the first file object
files[0]

{'versions': [{'size': 122880,
   'sha256': '3f38c4a6a79f9078f93d7e56fb4ba4f1269385347eda77bf11f14fb360021ad4',
   'version_id': 'mv06n4PtxvQcYTniTC1BrOTMLgMWOMg',
   'last_modified': '23.11.2022 09:13:28 UTC',
   'is_latest': True,
   'display': 'v20221123091328'},
  {'size': 122880,
   'sha256': '1fb213ceeb68144624cd21d907df912049d260b245da49218974ffa8364bbf86',
   'version_id': 'jfw26Yq90D4QBoWtHgSLHxuUb4xBTit',
   'last_modified': '23.11.2022 09:09:30 UTC',
   'is_latest': False,
   'display': 'v20221123090930'},
  {'size': 122880,
   'sha256': 'e6b274430ee77f0dfc384b025a63556d643eed9fcead4959a5ad4b568cb97e19',
   'version_id': 'VDNMiPv.Naf5Uf7EekPZrKT0Kc1h8Ag',
   'last_modified': '23.11.2022 06:45:09 UTC',
   'is_latest': False,
   'display': 'v20221123064509'}],
 'name': 'data.gpkg',
 'size': 122880,
 'sha256': '3f38c4a6a79f9078f93d7e56fb4ba4f1269385347eda77bf11f14fb360021ad4',
 'last_modified': '23.11.2022 09:13:28 UTC'}

In [26]:
# print filenames
for i in files:
    print(i["name"])

data.gpkg
fiji-osm.mbtiles
fiji-tikina-2017.gpkg
lulc-ground-truth_cloud.qgs


### Download files

We can use the `download_file()` method to download a specified file from QFieldCloud. 

The `download_file()` method has `project_id`, `remote_filename`, `local_filename`, `download_type`, and `show_progress` parameters.

The `local_filename` parameter expects a `Path` object from the `pathlib` module. 

The qfieldcloud-sdk has a `FileTransferType` class which specifies whether we want the `PROJECT` or `PACKAGE` files. Here, we want the `PROJECT` files. 

Let's download `data.gpkg` which stores the ground truth points collected in the field using QField.

In [71]:
# Create a path object for the file to download
local_filename = Path(os.path.join(os.getcwd(), "data.gpkg"))

# Download the file from QFieldCloud
client.download_file(
    project_id="2127b0a8-ced6-4129-a56b-4e8edf332d3d",
    remote_filename="data.gpkg",
    local_filename=local_filename,
    download_type=sdk.FileTransferType.PROJECT,
    show_progress=False
)

<Response [200]>

In [72]:
# Check data.gpkg downloaded OK
print(f"downloaded data.gpkg successfully: {'data.gpkg' in os.listdir()}")

downloaded data.gpkg successfully: True


### Visualise data

Now we have downloaded data from the QFieldCloud API we can visualise and analyse it. First, let's explore the data using charts and web map widgets.

In [73]:
# Read the data into a GeoPandas GeoDataFrame
gdf = gpd.read_file(os.path.join(os.getcwd(), "data.gpkg"))

First, let's inspect the data in data table.

In [74]:
display(gdf)

point_id surveyor            date_time  \
0    {159f9091-9fc6-49b3-8a40-38a7ccca222f}     test  2022-11-23T10:15:39   
1    {1183a29f-7fe9-4938-8fec-66f1531ce8c2}     test  2022-11-23T10:15:52   
2    {4f213bd4-49f1-4583-970f-aa8595f59211}     test  2022-11-23T10:15:59   
3    {72c80771-dbb9-45a2-a7ea-37aa20e916d3}     test  2022-11-23T10:16:05   
4    {daf89fc7-21d3-4db4-b402-b4b3b2fcb946}     test  2022-11-23T10:16:11   
..                                      ...      ...                  ...   
109  {f9c63ec0-551d-49c1-8e2d-6c7152356b96}     test  2022-11-23T17:11:54   
110  {76d40870-1b59-40b8-b7ce-27e7fc0d8a5f}     test  2022-11-23T17:12:04   
111  {ab0e0e06-6643-46f4-bf3d-dcfb727d7e8d}     test  2022-11-23T17:12:35   
112  {ab208318-eeca-4ea3-a52d-5be58d29f41a}     test  2022-11-23T17:12:54   
113  {7aae54e1-d38c-4c9a-aba4-9a7d49636119}     test  2022-11-23T17:13:06   

    land_cover_class horizontal_accuracy direction notes photo  \
0                  2                None      None  None  None   
1                  2                None      None  None  None   
2                  2                None      None  None  None   
3                  6                None      None  None  None   
4                  6                None      None  None  None   
..               ...                 ...       ...   ...   ...   
109                3                None      None  None  None   
110                3                None      None  None  None   
111                3                None      None  None  None   
112                3                None      None  None  None   
113                3                None      None  None  None   

                        geometry  
0    POINT (178.47209 -18.12624)  
1    POINT (178.47221 -18.12556)  
2    POINT (178.47241 -18.12714)  
3    POINT (178.47042 -18.12791)  
4    POINT (178.47099 -18.12804)  
..                           ...  
109  POINT (178.35100 -18.11237)  
110  POINT (178.35017 -18.11135)  
111  POINT (178.37205 -18.11716)  
112  POINT (178.36994 -18.11591)  
113  POINT (178.36893 -18.11613)  

[114 rows x 9 columns]

Next, let's create interactive visualisations using the data downloaded from QFieldCloud. We'll use <a href="https://plotly.com/python/plotly-express/" target="_blank">Plotly Express</a> to create interactive figures and web maps. 

We can use the `px.histogram()` function to create a bar plot of the counts of observations for each land cover class in our QFieldCloud project.

In [112]:
color_discrete_map={
    "1": "#00097B",
    "2": "#04e3a5",
    "3": "#8a6d1d",
    "4": "#ffffff",
    "5": "#ff9143",
    "6": "#d0ff14",
    "7": "#a4c93f",
    "8": "#377d22"}

fig = px.histogram(
    gdf, 
    x="land_cover_class", 
    color="land_cover_class",
    color_discrete_map=color_discrete_map, 
    title="Number of observations per-land cover class",
    labels={"land_cover_class": "land cover class"}
)

fig.update_layout(
    xaxis = dict(
        tickmode = "array",
        tickvals = [1, 2, 3, 4, 5, 6, 7, 8],
        ticktext = ["water", "mangrove", "bare soil", "urban", "cropland", "grassland", "shrubland", "trees"]
    )
)

fig.show()

Next, let's visualise the data in our QFieldCloud project on a web map using the `px.scatter_mapbox()` function.

In [134]:
color_discrete_map={
    "1": "#00097B",
    "2": "#04e3a5",
    "3": "#8a6d1d",
    "4": "#ffffff",
    "5": "#ff9143",
    "6": "#d0ff14",
    "7": "#a4c93f",
    "8": "#377d22"}

fig = px.scatter_mapbox(
    gdf,
    lat=gdf.geometry.y,
    lon=gdf.geometry.x,
    zoom=12,
    mapbox_style="open-street-map",
    color="land_cover_class",
    color_discrete_map=color_discrete_map
)

fig.show()

### Accuracy Assessment

Here, we'll use the ground truth data that we've collected in the field using QField to perform a quick accuracy assessment of the ESA World Cover v200 land cover map.

Let's download clip of the ESA World Cover v200 land cover map that covers Suva and the surrounding area.

In [85]:
!wget "https://github.com/livelihoods-and-landscapes/pacific-geo-conf/raw/main/esa-world-cover-v2-suva.tif"

--2022-11-23 11:02:46--  https://github.com/livelihoods-and-landscapes/pacific-geo-conf/raw/main/esa-world-cover-v2-suva.tif
Resolving github.com (github.com)... 192.30.255.112
Connecting to github.com (github.com)|192.30.255.112|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/livelihoods-and-landscapes/pacific-geo-conf/main/esa-world-cover-v2-suva.tif [following]
--2022-11-23 11:02:47--  https://raw.githubusercontent.com/livelihoods-and-landscapes/pacific-geo-conf/main/esa-world-cover-v2-suva.tif
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 98102 (96K) [image/tiff]
Saving to: ‘esa-world-cover-v2-suva.tif’

esa-world-cover-v2- 100%[===================>]  95.80K  --.-KB/s    in 0.01s   

2022

Sample the ESA World Cover v2 land cover class at each location where we've collected a ground truth point. Append the predicted class as a column to our `GeoDataFrame` `gdf`. 

In [102]:
# based on https://geopandas.org/en/stable/gallery/geopandas_rasterio_sample.html
coord_list = [(x,y) for x,y in zip(gdf["geometry"].x , gdf["geometry"].y)]

with rasterio.open(os.path.join(os.getcwd(), "esa-world-cover-v2-suva.tif")) as src:
    meta = src.meta
    img = src.read(1)
    gdf["predicted_land_cover"] = [str(x[0]) for x in src.sample(coord_list)]

In [104]:
display(gdf)

point_id surveyor            date_time  \
0    {159f9091-9fc6-49b3-8a40-38a7ccca222f}     test  2022-11-23T10:15:39   
1    {1183a29f-7fe9-4938-8fec-66f1531ce8c2}     test  2022-11-23T10:15:52   
2    {4f213bd4-49f1-4583-970f-aa8595f59211}     test  2022-11-23T10:15:59   
3    {72c80771-dbb9-45a2-a7ea-37aa20e916d3}     test  2022-11-23T10:16:05   
4    {daf89fc7-21d3-4db4-b402-b4b3b2fcb946}     test  2022-11-23T10:16:11   
..                                      ...      ...                  ...   
109  {f9c63ec0-551d-49c1-8e2d-6c7152356b96}     test  2022-11-23T17:11:54   
110  {76d40870-1b59-40b8-b7ce-27e7fc0d8a5f}     test  2022-11-23T17:12:04   
111  {ab0e0e06-6643-46f4-bf3d-dcfb727d7e8d}     test  2022-11-23T17:12:35   
112  {ab208318-eeca-4ea3-a52d-5be58d29f41a}     test  2022-11-23T17:12:54   
113  {7aae54e1-d38c-4c9a-aba4-9a7d49636119}     test  2022-11-23T17:13:06   

    land_cover_class horizontal_accuracy direction notes photo  \
0                  2                None      None  None  None   
1                  2                None      None  None  None   
2                  2                None      None  None  None   
3                  6                None      None  None  None   
4                  6                None      None  None  None   
..               ...                 ...       ...   ...   ...   
109                3                None      None  None  None   
110                3                None      None  None  None   
111                3                None      None  None  None   
112                3                None      None  None  None   
113                3                None      None  None  None   

                        geometry predicted_land_cover  
0    POINT (178.47209 -18.12624)                    2  
1    POINT (178.47221 -18.12556)                    2  
2    POINT (178.47241 -18.12714)                    2  
3    POINT (178.47042 -18.12791)                    6  
4    POINT (178.47099 -18.12804)                    6  
..                           ...                  ...  
109  POINT (178.35100 -18.11237)                    6  
110  POINT (178.35017 -18.11135)                    6  
111  POINT (178.37205 -18.11716)                    6  
112  POINT (178.36994 -18.11591)                    2  
113  POINT (178.36893 -18.11613)                    2  

[114 rows x 10 columns]

In [107]:
# accuracy score
print(f"the accuracy score for the ESA World Cover v2 land cover map is {round(accuracy_score(gdf['land_cover_class'], gdf['predicted_land_cover']), 2)}")


the accuracy score for the ESA World Cover v2 land cover map is 0.64


In [113]:
# quick look at the land cover map to check it seems OK
px.imshow(img)

Finally, we can visualise a confusion matrix as a heatmap. 

In [133]:
fig = px.density_heatmap(
    gdf,
    x="land_cover_class",
    y="predicted_land_cover",
    text_auto=True,
    labels={"land_cover_class": "land cover class",
            "predicted_land_cover": "ESA World Cover prediction"}
)

fig.update_layout(
    xaxis = dict(
        tickmode = "array",
        tickvals = [1, 2, 3, 4, 5, 6, 7, 8],
        ticktext = ["water", "mangrove", "bare soil", "urban", "cropland", "grassland", "shrubland", "trees"]
    ),
    yaxis = dict(
        tickmode = "array",
        tickvals = [1, 2, 3, 4, 6, 8],
        ticktext = ["water", "mangrove", "bare soil", "urban", "grassland", "trees"]
    )
)

fig.show()
